## Loading Dataset

In [1]:
import pandas as pd

FILENAME = "btc_5min.csv"          # ← use your real file name or path

# 1. Read and parse the data
df = (pd.read_csv(FILENAME,
                  parse_dates=["datetime"])       # make sure the column is really called “datetime”
        .sort_values("datetime")
        .set_index("datetime"))

# 2. Convert local timestamps → UTC  (gmtoffset is in seconds)
df.index = df.index - pd.to_timedelta(df["gmtoffset"], unit="s")
df.drop(columns="gmtoffset", inplace=True)


In [2]:
# 3️⃣  Quick sanity check
df.head()


timestamp           open           high  \
2025-05-30 00:00:00+00:00  1748563200  105593.250000  105727.351562   
2025-05-30 00:05:00+00:00  1748563500  105730.406250  105866.625000   
2025-05-30 00:10:00+00:00  1748563800  105881.734375  105896.656250   
2025-05-30 00:15:00+00:00  1748564100  105918.382812  105985.171875   
2025-05-30 00:20:00+00:00  1748564400  105959.453125  106071.843750   

                                     low          close       volume  
2025-05-30 00:00:00+00:00  105593.250000  105727.351562          NaN  
2025-05-30 00:05:00+00:00  105730.406250  105866.625000  178528256.0  
2025-05-30 00:10:00+00:00  105876.710937  105896.656250          NaN  
2025-05-30 00:15:00+00:00  105918.382812  105981.375000          NaN  
2025-05-30 00:20:00+00:00  105959.453125  106071.843750   97390592.0

In [3]:
df.info(show_counts=True)

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 34429 entries, 2025-05-30 00:00:00+00:00 to 2025-09-26 03:29:00+00:00
Data columns (total 6 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   timestamp  34429 non-null  int64  
 1   open       33980 non-null  float64
 2   high       33980 non-null  float64
 3   low        33980 non-null  float64
 4   close      33980 non-null  float64
 5   volume     18210 non-null  float64
dtypes: float64(5), int64(1)
memory usage: 1.8 MB


## Dealing with missing prices and volumes, towards continuous dataframe

In [19]:
# Forward-fill price gaps (standard practice for OHLC data)
price_cols = ["open", "high", "low", "close"]
df[price_cols] = df[price_cols].ffill()

# Forward-fill volume OR replace with 0 if “no trades” makes sense
df["volume"] = df["volume"].fillna(0.0)

# Verify we’re clean
df.isnull().sum()


timestamp    0
open         0
high         0
low          0
close        0
volume       0
dtype: int64

In [4]:
# 5-minute spacing should equal 300 s
gaps = df.index.to_series().diff().dt.total_seconds().ne(300).sum()
print(f"Missing 5-min bars: {gaps}")

# Basic stats
print(df.describe(include='all').T)


Missing 5-min bars: 230
             count          mean           std           min           25%  \
timestamp  34429.0  1.753710e+09  2.971699e+06  1.748563e+09  1.751136e+09   
open       33980.0  1.121732e+05  5.181268e+03  9.844307e+04  1.077426e+05   
high       33980.0  1.122095e+05  5.182161e+03  9.856961e+04  1.077833e+05   
low        33980.0  1.121369e+05  5.179991e+03  9.838677e+04  1.077087e+05   
close      33980.0  1.121735e+05  5.181153e+03  9.838677e+04  1.077502e+05   
volume     18210.0  6.218424e+08  1.599163e+09  8.192000e+03  6.048870e+07   

                    50%           75%           max  
timestamp  1.753709e+09  1.756283e+09  1.758857e+09  
open       1.126113e+05  1.168757e+05  1.242106e+05  
high       1.126536e+05  1.169065e+05  1.243223e+05  
low        1.125698e+05  1.168388e+05  1.242106e+05  
close      1.126121e+05  1.168768e+05  1.243006e+05  
volume     2.610616e+08  9.294776e+08  4.812227e+10  


In [5]:
import pandas as pd

# df already contains the 34,429 rows you loaded, indexed by UTC timestamp
# -----------------------------------------------------------------------
# 1. Build the full 5-minute index from first to last timestamp
full_idx = pd.date_range(start=df.index.min(),
                         end=df.index.max(),
                         freq="5min")

# 2. Re-index → missing bars appear as NaN rows
df = df.reindex(full_idx)

# 3. Forward-fill price columns; set missing volume to 0
price_cols = ["open", "high", "low", "close"]
df[price_cols] = df[price_cols].ffill()
df["volume"]   = df["volume"].fillna(0.0)

# Sanity check
print("Remaining NaNs in open:", df["open"].isna().sum())   # should be 0
print("Row count after fill :", len(df))                    # 34,659 (=34,429+230)


Remaining NaNs in open: 0
Row count after fill : 34314


## Labelling and feature engineering

In [6]:
# --- PARAMETERS ----------------------------------------------------------
LOOKBACK   = 40        # 200 min window
MULTIPLIER = 3         # 3× average absolute return

# --- 1. CREATE TARGET ----------------------------------------------------
df["ret"]         = df["close"].pct_change()
df["avg_abs_ret"] = df["ret"].abs().rolling(LOOKBACK, min_periods=LOOKBACK).mean()
df["breakout"]    = (df["ret"].abs() >= MULTIPLIER*df["avg_abs_ret"]).astype(int)

# Drop the first LOOKBACK rows that still have NaN in avg_abs_ret
df.dropna(subset=["avg_abs_ret"], inplace=True)

print("Class balance:")
print(df["breakout"].value_counts(normalize=True))

# --- 2. BASIC PRICE-ONLY FEATURES ---------------------------------------
# Time features
df["minute"] = df.index.minute
df["hour"]   = df.index.hour
df["dow"]    = df.index.dayofweek          # 0=Mon … 6=Sun

# Rolling volatility & momentum (1 h, 3 h, 6 h)
for w in [12, 36, 72]:
    df[f"vol_{w}"] = df["ret"].rolling(w).std()
    df[f"mom_{w}"] = df["close"].pct_change(w)

# Candle shape
df["body_pct"]  = (df["close"] - df["open"]).abs() / (df["high"] - df["low"])
df["upper_pct"] = (df["high"] - df[["open","close"]].max(axis=1)) / (df["high"] - df["low"])
df["lower_pct"] = (df[["open","close"]].min(axis=1) - df["low"]) / (df["high"] - df["low"])

df.dropna(inplace=True)                    # remove rows with fresh NaNs

# --- 3. READY FOR MODELING ----------------------------------------------
FEATURES = [c for c in df.columns
            if c not in ["breakout", "ret", "avg_abs_ret"]]

print(f"{len(FEATURES)} feature columns prepared.  Example rows:")
display(df.head())


Class balance:
breakout
0    0.953959
1    0.046041
Name: proportion, dtype: float64
18 feature columns prepared.  Example rows:


timestamp           open           high  \
2025-05-30 09:20:00+00:00  1748596800  105280.390625  105339.656250   
2025-05-30 09:25:00+00:00  1748597100  105355.679687  105355.679687   
2025-05-30 09:30:00+00:00  1748597400  105298.632812  105298.632812   
2025-05-30 09:35:00+00:00  1748597700  105196.375000  105221.468750   
2025-05-30 09:40:00+00:00  1748598000  104868.015625  104885.203125   

                                     low          close       volume  \
2025-05-30 09:20:00+00:00  105280.390625  105328.820312    8556544.0   
2025-05-30 09:25:00+00:00  105307.117187  105307.117187          0.0   
2025-05-30 09:30:00+00:00  105181.171875  105181.171875   14508032.0   
2025-05-30 09:35:00+00:00  105052.562500  105052.562500          0.0   
2025-05-30 09:40:00+00:00  104660.796875  104885.203125  383787008.0   

                                ret  avg_abs_ret  breakout  minute  ...  dow  \
2025-05-30 09:20:00+00:00  0.000378     0.000885         0      20  ...    4   
2025-05-30 09:25:00+00:00 -0.000206     0.000885         0      25  ...    4   
2025-05-30 09:30:00+00:00 -0.001196     0.000907         0      30  ...    4   
2025-05-30 09:35:00+00:00 -0.001223     0.000919         0      35  ...    4   
2025-05-30 09:40:00+00:00 -0.001593     0.000957         0      40  ...    4   

                             vol_12    mom_12    vol_36    mom_36    vol_72  \
2025-05-30 09:20:00+00:00  0.001049  0.003591  0.001212 -0.006665  0.000923   
2025-05-30 09:25:00+00:00  0.000770  0.000802  0.001211 -0.006344  0.000920   
2025-05-30 09:30:00+00:00  0.000818 -0.001126  0.001223 -0.007261  0.000928   
2025-05-30 09:35:00+00:00  0.000867 -0.001674  0.001234 -0.008172  0.000937   
2025-05-30 09:40:00+00:00  0.000934 -0.003777  0.001254 -0.009213  0.000953   

                             mom_72  body_pct  upper_pct  lower_pct  
2025-05-30 09:20:00+00:00 -0.007058  0.817163   0.182837   0.000000  
2025-05-30 09:25:00+00:00 -0.007780  1.000000   0.000000   0.000000  
2025-05-30 09:30:00+00:00 -0.009054  1.000000   0.000000   0.000000  
2025-05-30 09:35:00+00:00 -0.010210  0.851434   0.148566   0.000000  
2025-05-30 09:40:00+00:00 -0.011575  0.076591   0.000000   0.923409  

[5 rows x 21 columns]

## Checking the classes balance

In [7]:
# --- class balance -------------------------------------------------------
balance = (
    df["breakout"]           # 1 = breakout, 0 = normal bar
      .value_counts(normalize=True)   # fraction of total
      .mul(100)                       # → %
)

print("Class balance (% of bars):")
print(f"  Non-breakout (0): {balance.loc[0]:5.2f}%")
print(f"  Breakout    (1): {balance.loc[1]:5.2f}%")



Class balance (% of bars):
  Non-breakout (0): 95.36%
  Breakout    (1):  4.64%


## Choosing the model 

In [8]:
# ---------- 0.  Feature matrix and target -----------------
FEATURES = [
    "close", "volume",           # raw
    "ret", "avg_abs_ret",        # already in df
    "mom_12","mom_36","mom_72",  # add your engineered columns here
    "vol_12","vol_36","vol_72",
    "body_pct","upper_pct","lower_pct",
    "hour","minute","dow"
]

X = df[FEATURES]
y = df["breakout"]

# ---------- 1.  Chronological splits ----------------------
train_end = int(len(df)*0.70)
val_end   = int(len(df)*0.85)

X_train, y_train = X.iloc[:train_end],       y.iloc[:train_end]
X_val,   y_val   = X.iloc[train_end:val_end],y.iloc[train_end:val_end]
X_test,  y_test  = X.iloc[val_end:],         y.iloc[val_end:]

print(f"Train:{len(X_train)}  Val:{len(X_val)}  Test:{len(X_test)}")

# ---------- 2.  Check class balance -----------------------
balance = y_train.value_counts(normalize=True).mul(100)
print("\nTrain-set class balance:")
print(f"  Non-breakout (0): {balance.loc[0]:5.2f}%")
print(f"  Breakout    (1): {balance.loc[1]:5.2f}%")



Train:23751  Val:5090  Test:5090

Train-set class balance:
  Non-breakout (0): 95.27%
  Breakout    (1):  4.73%


In [12]:
from lightgbm import LGBMClassifier, log_evaluation

clf = LGBMClassifier(
        n_estimators=600,
        learning_rate=0.05,
        num_leaves=31,
        subsample=0.8,
        colsample_bytree=0.8,
        class_weight={0:1, 1:weight},   # imbalance fix
        objective="binary",
        verbosity=-1                    # −1 = silent
)

clf.fit(
    X_train, y_train,
    eval_set=[(X_val, y_val)],
    eval_metric="aucpr",
    callbacks=[log_evaluation(period=25)]   # print every 25 rounds
)



[25]	valid_0's binary_logloss: 0.198106
[50]	valid_0's binary_logloss: 0.0849949
[75]	valid_0's binary_logloss: 0.0487376
[100]	valid_0's binary_logloss: 0.0325402
[125]	valid_0's binary_logloss: 0.0256049
[150]	valid_0's binary_logloss: 0.0214363
[175]	valid_0's binary_logloss: 0.0193791
[200]	valid_0's binary_logloss: 0.0180072
[225]	valid_0's binary_logloss: 0.0176936
[250]	valid_0's binary_logloss: 0.017499
[275]	valid_0's binary_logloss: 0.0174013
[300]	valid_0's binary_logloss: 0.0173757
[325]	valid_0's binary_logloss: 0.0176512
[350]	valid_0's binary_logloss: 0.0175439
[375]	valid_0's binary_logloss: 0.01773
[400]	valid_0's binary_logloss: 0.0178965
[425]	valid_0's binary_logloss: 0.0180023
[450]	valid_0's binary_logloss: 0.0182186
[475]	valid_0's binary_logloss: 0.0185264
[500]	valid_0's binary_logloss: 0.0186016
[525]	valid_0's binary_logloss: 0.018768
[550]	valid_0's binary_logloss: 0.019127
[575]	valid_0's binary_logloss: 0.019431
[600]	valid_0's binary_logloss: 0.019888


LGBMClassifier(class_weight={0: 1, 1: np.float64(20.14959928762244)},
               colsample_bytree=0.8, learning_rate=0.05, n_estimators=600,
               objective='binary', subsample=0.8, verbosity=-1)

In [13]:
best_iter = clf.best_iteration_   # or just 300 if .best_iteration_ unavailable


In [14]:
from sklearn.metrics import precision_recall_curve, f1_score

probs_val = clf.predict_proba(X_val)[:,1]
precision, recall, thr = precision_recall_curve(y_val, probs_val)
f1 = 2*precision*recall / (precision+recall+1e-12)
best_thr = thr[f1.argmax()]          # often lands around 0.10–0.25


In [16]:
import pandas as pd
import numpy as np
# append an extra 1.0 so threshold list matches precision/recall length
res = pd.DataFrame({
        "threshold" : np.append(thr, 1),    # thr is len-1 compared with precision/recall
        "precision" : precision,
        "recall"    : recall,
        "F1"        : f1
})

# sort so the best rows appear first
res = res.sort_values("F1", ascending=False).reset_index(drop=True)

print("Top 10 threshold candidates")
display(res.head(10))

best_thr = res.loc[0, "threshold"]
best_f1  = res.loc[0, "F1"]
print(f"\nBest threshold = {best_thr:.3f}   (F1 = {best_f1:.3f})")


Top 10 threshold candidates


threshold  precision    recall        F1
0   0.728868   0.955882  0.924171  0.939759
1   0.713430   0.951220  0.924171  0.937500
2   0.769374   0.955665  0.919431  0.937198
3   0.810878   0.960199  0.914692  0.936893
4   0.858565   0.964824  0.909953  0.936585
5   0.705587   0.946602  0.924171  0.935252
6   0.771967   0.955446  0.914692  0.934625
7   0.832506   0.960000  0.909953  0.934307
8   0.867943   0.964646  0.905213  0.933985
9   0.647981   0.937799  0.928910  0.933333


Best threshold = 0.729   (F1 = 0.940)


In [17]:
import matplotlib.pyplot as plt

plt.figure(figsize=(6,4))
plt.step(recall, precision, where="post", label="P-R curve")
plt.scatter(recall[f1.argmax()], precision[f1.argmax()],
            color="red", zorder=3,
            label=f"best thr={best_thr:.3f}\nF1={best_f1:.3f}")
plt.xlabel("Recall")
plt.ylabel("Precision")
plt.title("Precision–Recall curve (validation set)")
plt.legend()
plt.grid(True)
plt.show()


In [18]:
plt.figure(figsize=(6,3))
plt.plot(thr, f1[:-1], marker=".")
plt.axvline(best_thr, color="red", ls="--")
plt.xlabel("Threshold")
plt.ylabel("F1 score")
plt.title("F1 vs. probability threshold")
plt.show()


In [20]:
import joblib

joblib.dump(clf, "breakout_detector.pkl")   # ← saves 30 kB-ish file


['breakout_detector.pkl']

In [21]:
THRESHOLD = 0.73     # from your PR-curve sweep
FEE       = 0.0005   # 0.05 % per side
HOLD      = 3        # bars
equity    = 1.0
trades    = []
pos       = None

for ts,row in df.iterrows():                  # df is your full feature set
    prob  = clf.predict_proba(row[FEATURES].values.reshape(1,-1))[0,1]

    # exit block
    if pos:
        pos["bars"] += 1
        if pos["bars"] >= HOLD:
            ret = row.close/pos["price"] - 1 - 2*FEE
            equity *= 1+ret
            trades.append(ret)
            pos = None

    # entry block
    if (prob >= THRESHOLD) and (pos is None):
        pos = {"price": row.close, "bars": 0}

print(f"Final equity : {equity:.3f}×")
print(f"Total trades : {len(trades)}")
if trades:
    hit = sum(t>0 for t in trades)/len(trades)
    print(f"Hit ratio   : {hit:.2%}")


/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


Final equity : 0.301×
Total trades : 1254
Hit ratio   : 24.00%


/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/home/slmar/data_acq/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


In [22]:
# ONE call, no warnings
sample = X_test.iloc[[i]]          # retains column names
prob   = clf.predict_proba(sample)[0,1]


NameError: name 'i' is not defined

In [23]:
import joblib, pandas as pd, numpy as np
clf  = joblib.load("breakout_detector.pkl")        # ↩ your saved LightGBM
df   = pd.read_parquet("btc_5min_features.parquet")# ↩ feature-ready file

FEATURES = [                   # same 18 columns used in training
    "close","volume","ret","avg_abs_ret",
    "mom_12","mom_36","mom_72",
    "vol_12","vol_36","vol_72",
    "body_pct","upper_pct","lower_pct",
    "hour","minute","dow"
]


ImportError: Unable to find a usable engine; tried using: 'pyarrow', 'fastparquet'.
A suitable version of pyarrow or fastparquet is required for parquet support.
Trying to import the above resulted in these errors:
 - Missing optional dependency 'pyarrow'. pyarrow is required for parquet support. Use pip or conda to install pyarrow.
 - Missing optional dependency 'fastparquet'. fastparquet is required for parquet support. Use pip or conda to install fastparquet.